In [26]:
## import libraries
import sys
import glob
import re

import cartopy
import matplotlib.pyplot as plt
import numpy as np
import xarray as xr
import pandas as pd
import cmocean.cm as cmo
from matplotlib.gridspec import GridSpec
from matplotlib.colorbar import Colorbar # different way to handle colorbar
import geopandas as gpd

# cartopy
import cartopy.crs as ccrs
import cartopy.feature as cfeature
from scipy.ndimage import gaussian_filter    # smoothing contour lines

# import personal modules
# Path to modules
sys.path.append('../modules')
# Import my modules
from plotter import draw_basemap, plot_terrain
from utils import roundPartial, select_months_ds

pd.options.display.float_format = "{:,.2f}".format # makes it so pandas tables display only first two decimals

In [2]:
path_to_data = '/data/projects/Comet/cwp140/' 
path_to_out  = '../out/'       # output files (numerical results, intermediate datafiles) -- read & write
path_to_figs = '../figs/'      # figures

In [6]:
## load cluster results
df_lst = []
for i in range(1, 5):
    fname = path_to_data + 'preprocessed/suma/Cluster{0}_PRISM_CO_Watershed_90th_percentile_precip_dates.csv'.format(i)
    df = pd.read_csv(fname)
    df = df.rename(columns={"# Cluster{0}_date".format(i): "date"})
    df['date'] = pd.to_datetime(df['date'])
    df['cluster'] = i
    df_lst.append(df)
df = pd.concat(df_lst, ignore_index=True)
df.set_index('date', inplace=True)
df

cluster
date               
2000-01-27        1
2000-02-18        1
2000-03-16        1
2000-03-21        1
2000-03-31        1
...             ...
2019-10-05        4
2019-11-21        4
2019-11-26        4
2019-11-30        4
2019-12-28        4

[1388 rows x 1 columns]

In [10]:
## load pcp data
fname = path_to_data + 'preprocessed/suma/pcp.nc'
prec = xr.open_dataset(fname)

fname = path_to_data + 'preprocessed/suma/ivt_*_00UTC.nc'
ivt = xr.open_mfdataset(fname)
ivt = ivt.rename({"p71.162": "uIVT", "p72.162": "vIVT"})
IVT = np.sqrt(ivt['uIVT']**2 + ivt['vIVT']**2)
ivt = ivt.assign(IVT=IVT)
ivt

/home/dnash/miniconda3/envs/SEAK-clim/lib/python3.10/site-packages/xarray/coding/times.py:150: SerializationWarning: Ambiguous reference date string: 1-1-1 00:00:00. The first value is assumed to be the year hence will be padded with zeros to remove the ambiguity (the padded reference date string is: 0001-1-1 00:00:00). To remove this message, remove the ambiguity by padding your reference date strings with zeros.
  warnings.warn(warning_msg, SerializationWarning)


<xarray.Dataset>
Dimensions:    (longitude: 321, latitude: 201, time: 7671)
Coordinates:
  * longitude  (longitude) float32 -130.0 -129.8 -129.5 ... -50.5 -50.25 -50.0
  * latitude   (latitude) float32 60.0 59.75 59.5 59.25 ... 10.5 10.25 10.0
  * time       (time) datetime64[ns] 2000-01-01 2000-01-02 ... 2020-12-31
Data variables:
    uIVT       (time, latitude, longitude) float32 dask.array<chunksize=(7671, 201, 321), meta=np.ndarray>
    vIVT       (time, latitude, longitude) float32 dask.array<chunksize=(7671, 201, 321), meta=np.ndarray>
    IVT        (time, latitude, longitude) float32 dask.array<chunksize=(7671, 201, 321), meta=np.ndarray>
Attributes:
    Conventions:  CF-1.6
    history:      2023-07-25 01:01:28 GMT by grib_to_netcdf-2.25.1: /opt/ecmw...

In [11]:
## for each cluster type, make a subset of the dataset
ds_lst = []
prec_lst = []
for i in range(1, 5):
    idx = (df.cluster == i)
    dates = df.loc[idx].index.values

    ds_lst.append(ivt.sel(time=dates).mean('time'))
    prec_lst.append(prec.sel(time=dates).mean('time'))

In [23]:
## Load Basin watershed file
fp = path_to_data + 'downloads/UpperCO/Upper_Colorado_River_Basin_Boundary/Upper_Colorado_River_Basin_Boundary.shp'
basin = gpd.read_file(fp, crs="EPSG:4326") # have to manually set the projection
basin

EXT_ID  EXT_TYP_ID                   NAME  \
0    9389        5.00  Upper Colorado Region   

                                            geometry  
0  POLYGON ((-106.65587 40.51559, -106.65376 40.5...

In [35]:
# contour labels
kw_clabels = {'fontsize': 7, 'inline': True, 'inline_spacing': 7, 'fmt': '%i',
              'rightside_up': True, 'use_clabeltext': True}

ext = [-130., -90., 25., 50.] 
fmt = 'png'

# Set up projection
datacrs = ccrs.PlateCarree()  ## the projection the data is in
mapcrs = ccrs.PlateCarree() ## the projection you want your map displayed in

# Set tick/grid locations
tx = 10
ty = 5
dx = np.arange(ext[0],ext[1]+tx,tx)
dy = np.arange(ext[2],ext[3]+ty,ty)

nrows = 2
ncols = 5

## Use gridspec to set up a plot with a series of subplots that is
## n-rows by n-columns
gs = GridSpec(nrows, ncols, height_ratios=[1, 1], width_ratios = [1, 1, 1, 1, 0.05], wspace=0.01, hspace=0.1)
## use gs[rows index, columns index] to access grids

fig = plt.figure(figsize=(31.0 ,12.))
fig.dpi = 600
fname = path_to_figs + 'synoptic_maps_clusters'

# Add color bar axis
cbax = plt.subplot(gs[0,-1]) # colorbar axis

col_idx = [0, 1, 2, 3]
llat_lst = [True, False, False, False]
lbls = ['Cluster 1', 'Cluster 2', 'Cluster 3', 'Cluster 4']
for i, (ds, prec) in enumerate(zip(ds_lst, prec_lst)):
    ax = fig.add_subplot(gs[0,col_idx[i]], projection=mapcrs)
    ax = draw_basemap(ax, extent=ext, xticks=dx, yticks=dy,left_lats=llat_lst[i], right_lats=False)
    

    ax.add_feature(cfeature.STATES, edgecolor='0.4', linewidth=0.8)
    # ax.set_title(lbls[i], loc='left', fontsize=14)

    ## Plot IVT
    data = ds.IVT.values
    cmap = cmo.deep
    cflevs = np.arange(0, 500, 50)
    cf = ax.contourf(ds.longitude, ds.latitude, data, transform=datacrs,
                     levels=cflevs, cmap=cmap, alpha=0.8, extend='both')
    
    ## Plot IVT vectors
    # Wind barbs / vectors 
    uvec = ds.uIVT.values
    vvec = ds.vIVT.values

    Q = ax.quiver(ds.longitude, ds.latitude, uvec, vvec, transform=datacrs, 
              color='k', regrid_shape=20,
              angles='xy', scale_units='xy', scale=125, units='xy')

    ## add in focus watershed
    basin.plot(ax=ax, edgecolor='white', color='None', zorder=99)

    ax.set_extent(ext, datacrs)

cb = Colorbar(ax = cbax, mappable = cf, orientation = 'vertical', ticklocation = 'right')
cb.set_label('IVT (kg m$^{-1}$ s$^{-1}$)', fontsize=11)
cb.ax.tick_params(labelsize=12)

# Add color bar axis
cbax = plt.subplot(gs[1,-1]) # colorbar axis
ext = [-109.5, -101.5, 36.5, 41.5] # extent of CO
# Set tick/grid locations
tx = 2
ty = 1
dx = np.arange(-109.,-100.,tx)
dy = np.arange(36.,42.,ty)
for i, prec in enumerate(prec_lst):
    ax = fig.add_subplot(gs[1,col_idx[i]], projection=mapcrs)
    ax = draw_basemap(ax, extent=ext, xticks=dx, yticks=dy,left_lats=llat_lst[i], right_lats=False)
    

    ax.add_feature(cfeature.STATES, edgecolor='0.4', linewidth=0.8)
    # ax.set_title(lbls[i], loc='left', fontsize=14)

    ## Plot IVT
    data = prec.pcp.values
    cmap = cmo.rain
    cflevs = np.arange(2, 18, 2)
    cf = ax.contourf(prec.lon, prec.lat, data, transform=datacrs,
                     levels=cflevs, cmap=cmap, alpha=0.8, extend='max')

    ## add in focus watershed
    basin.plot(ax=ax, edgecolor='white', color='None', zorder=99)

    ax.set_extent(ext, datacrs)

cb = Colorbar(ax = cbax, mappable = cf, orientation = 'vertical', ticklocation = 'right')
cb.set_label('Precipitation (mm day$^{-1}$)', fontsize=11)
cb.ax.tick_params(labelsize=12)

fig.savefig('%s.%s' %(fname, fmt), bbox_inches='tight', dpi=fig.dpi, transparent=True)
plt.show()
fig.clf()